### Create the process for merging new or corrected site data

In [120]:
import geopandas as gpd
import pandas as pd
import numpy as np
import os
import folium
# use these if you are using the pandas dataframe view, I prefer itables because it is interactive
# pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)

# this makes dataframes viewable as interactive tables with search and sort
from itables import init_notebook_mode
init_notebook_mode(all_interactive=True)

import itables.options as opt
opt.maxBytes = 0 ### this removes size limits for interactive table


<IPython.core.display.Javascript object>

#### ** helpful links and snippets

In [ ]:
# os.getcwd() # check what the working directory is

# keyboard shortcuts
# https://noteable.io/blog/jupyter-notebook-shortcuts-boost-productivity/

### set working directory to the github repo directory
this is where you change this so that it works on your computer too

In [92]:
os.chdir('/Users/sarahodges/spatial/SAVI/hudson_access/data/published')

### Import existing site points data

 - this is actually the **hap_site_points_fieldupdates_surveyintegration_8-2-23.geojson** data from sara eichner, with the new entries removed from the dataset
 - using this to create the process of site data updates

In [154]:
current_site_points = gpd.read_file('data/archive/published_20230803/hap_site_points.geojson')
# len(current_site_points.columns)
current_site_points

site_id         act_codes                             access_id  \
0            174  FISH, HPBL, MPBL                      4, 516, 151, 787   
1             29  MPBL, HPBL, FISH                   126, 83, 1613, 1803   
2            183              FISH                      1, 443, 511, 800   
3             54  MPBL, HPBL, FISH     291, 433, 293, 166, 117, 000, 000   
4              1              HPBL  9, 097, 941, 594, 168, 710, 000, 000   
..           ...               ...                                   ...   
747  remove dupe              MPBL                                   509   
748          215              HPBL                     16, 752, 031, 621   
749        71975              HPBL                             1621_HPBL   
750          157  MPBL, HPBL, FISH                           3, 121, 599   
751          161              FISH                      1, 517, 201, 721   

                                site_name                   site_label  \
0                          Bayswater Park                         None   
1                   Conference House Park                         None   
2                 Mt Loretto Natural Area                         None   
3                        Lemon Creek Park                         None   
4                          Riverside Park                         None   
..                                    ...                          ...   
747                      River Barge Park                         None   
748             Gowanus Canal Sponge Park                         None   
749  Lowe's Gowanus Parklet & Boat Launch                         None   
750               Louis Valentino Jr Park                         None   
751                       Shore Road Park  Shore Road Park and Parkway   

                                          site_address  \
0    Dwight Ave, Seagirt Blvd between Beach 38th St...   
1    Hylan Blvd & Satterlee St, Staten Island, Hyla...   
2    End of Sharrotts Ave at Hylan Blvd, Hylan Blvd...   
3                                                 None   
4                             W 79th St End, Manhattan   
..                                                 ...   
747                                               None   
748               166 2nd St, Brooklyn, Foot of 2nd St   
749                   539 Smith St, Brooklyn, NY 11231   
750               End of Coffey St, Red Hook, Brooklyn   
751     Bay Ridge Ave (69th St) at Shore Rd, Bay Ridge   

                                      site_description  \
0    This waterfront park is named, in part, for Ju...   
1    The site of a legendary display of American de...   
2                                                 None   
3                             Yellow trail nature path   
4    This site is considered a cultural resource. R...   
..                                                 ...   
747                                               None   
748                                               None   
749                                               None   
750  Now surrounded by industrial, residential, and...   
751  An expansive park along the Shore Parkway Gree...   

                                    hours_info open_close_date   fee  ...  \
0    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
1    Sunrise to Sunset (April 1 to December 1)            None     Y  ...   
2                                         None            None  None  ...   
3                                         None            None  None  ...   
4    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
..                                         ...             ...   ...  ...   
747                                       None            None  None  ...   
748                                       None            None  None  ...   
749                                       None            None  None  ...   
750  Sunrise to Sunset (April 1 to December

In [1]:
### the site score was taken out of the current site points - see published 20230629 if you want to retrieve it
#### create a site_score dataframe and remove from data
# site_score = current_site_points.copy()[['site_id', 'site_score']]
#site_score.head()
# site_points.columns.to_list()

### Create site points dataframe and check highest id

In [157]:
# Filtering and Mutating operations
site_points = (
    current_site_points
    .query("site_id != '160223'")  ## remove dupe rockaways beach and boardwalk - Alyssa updates the other dupe too
    .query("site_id != 'remove dupe'")
    .drop(columns='site_score')  # Remove the 'site_score' column
    .assign(
        site_name=current_site_points["site_name"].where(current_site_points["site_name"] != "Fair Haven Rd & Fairwaters Lane", "Fair Haven Pier"),
        site_id=current_site_points["site_id"].where(current_site_points["site_name"] != "Fair Haven Rd & Fairwaters Lane", 540232),
        site_description=current_site_points['site_description'].str.replace('This site is considered an historic landmark', ''),
        url_public = current_site_points['url_public'].str.split(",").str[0]  ### keep only the first url if there is nore than one 
    )
)

# remove the extra Bayswater Point State Park
site_points = site_points[site_points["site_id"] != "159127"]
site_points.loc[site_points['site_id'] == '154', 'url_public'] = "https://www.nycgovparks.org/parks/leon-s-kaiser-park"


#site_points['site_id'] = pd.to_numeric(site_points['site_id'], errors='coerce')  
### the highest site_id (other than one that ends in 999 for a specific reason, is 900149)
highest = 900136

site_points_df = pd.DataFrame(site_points.drop(columns='geometry'))
site_points_df

site_id         act_codes                             access_id  \
0       174  FISH, HPBL, MPBL                      4, 516, 151, 787   
1        29  MPBL, HPBL, FISH                   126, 83, 1613, 1803   
2       183              FISH                      1, 443, 511, 800   
3        54  MPBL, HPBL, FISH     291, 433, 293, 166, 117, 000, 000   
4         1              HPBL  9, 097, 941, 594, 168, 710, 000, 000   
..      ...               ...                                   ...   
746      98  MPBL, FISH, HPBL                      6, 416, 501, 784   
748     215              HPBL                     16, 752, 031, 621   
749   71975              HPBL                             1621_HPBL   
750     157  MPBL, HPBL, FISH                           3, 121, 599   
751     161              FISH                      1, 517, 201, 721   

                                site_name                   site_label  \
0                          Bayswater Park                         None   
1                   Conference House Park                         None   
2                 Mt Loretto Natural Area                         None   
3                        Lemon Creek Park                         None   
4                          Riverside Park                         None   
..                                    ...                          ...   
746       Breezy Point Tip at Jamaica Bay                         None   
748             Gowanus Canal Sponge Park                         None   
749  Lowe's Gowanus Parklet & Boat Launch                         None   
750               Louis Valentino Jr Park                         None   
751                       Shore Road Park  Shore Road Park and Parkway   

                                          site_address  \
0    Dwight Ave, Seagirt Blvd between Beach 38th St...   
1    Hylan Blvd & Satterlee St, Staten Island, Hyla...   
2    End of Sharrotts Ave at Hylan Blvd, Hylan Blvd...   
3                                                 None   
4                             W 79th St End, Manhattan   
..                                                 ...   
746  End of Rockaway Point Blvd, Beach 222nd Street...   
748               166 2nd St, Brooklyn, Foot of 2nd St   
749                   539 Smith St, Brooklyn, NY 11231   
750               End of Coffey St, Red Hook, Brooklyn   
751     Bay Ridge Ave (69th St) at Shore Rd, Bay Ridge   

                                      site_description  \
0    This waterfront park is named, in part, for Ju...   
1    The site of a legendary display of American de...   
2                                                 None   
3                             Yellow trail nature path   
4    This site is considered a cultural resource. R...   
..                                                 ...   
746  It’s easy to forget one is in New York City at...   
748                                               None   
749                                               None   
750  Now surrounded by industrial, residential, and...   
751  An expansive park along the Shore Parkway Gree...   

                                    hours_info open_close_date   fee  ...  \
0    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
1    Sunrise to Sunset (April 1 to December 1)            None     Y  ...   
2                                         None            None  None  ...   
3                                         None            None  None  ...   
4    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
..                                         ...             ...   ...  ...   
746                                       None            None  None  ...   
748                                       None            None  None  ...   
749                                       None            None  None  ...   
750  Sunrise to Sunset (April 1 to December 1)            None  None  ...   
751                  

## IMPORT survey data from summer site visits and process
Alyssa collected these over the summer - up to July 28 using the Survey123 s

In [158]:
## add new survey data
raw_surv_new = pd.read_csv('data/staging/Hudson_Access_Project_Data_Survey_0.csv')

raw_surv_new

ObjectID                              GlobalID    county        lat  \
0         34  2446f541-de5b-4b1b-84d0-973d1f66cf4b     Kings  40.673157   
1         36  26b60cc7-0f57-49f6-8efa-e16ec0ddf0a2       NaN        NaN   
2         37  a0ac502e-6ea8-4c64-8ef5-c0e1ff10665e       NaN        NaN   
3         38  b9a61410-d38b-4e79-88ee-cfc5f723fb58       NaN        NaN   
4         39  29390baf-6222-415a-8ec2-2a8b8024c3d9     Kings  40.645092   
..       ...                                   ...       ...        ...   
58        94  c48c5370-3e9c-489f-8808-b2047c3e5575       NaN        NaN   
59        95  61f4f63a-7622-4267-8ca0-cb36872d2afb       NaN        NaN   
60        96  3909c237-197f-453e-8211-0d6454d25dbf  New York  40.819485   
61        97  0bebe570-9c68-42ee-8040-c98ffb8e61ce  New York  40.813918   
62        98  e1813fbf-48fa-45aa-85b6-be539e5a2937     Kings  40.676706   

          lon                                       municipality  \
0  -73.996983                                             Lowe's   
1         NaN                                                NaN   
2         NaN                                                NaN   
3         NaN                                                NaN   
4  -73.866486                                             Queens   
..        ...                                                ...   
58        NaN                                                NaN   
59        NaN                                                NaN   
60 -73.960644  Borough of Manhattan, New York County,New York...   
61 -73.934177                                      New York City   
62 -73.990100                             New York City,Brooklyn   

                                           natural_no   site_id  \
0                                              Lowe's   71975.0   
1                                                 NaN       NaN   
2                                                 NaN       NaN   
3                                                 NaN       NaN   
4                                              Queens  649119.0   
..                                                ...       ...   
58                                                NaN       NaN   
59                                                NaN      62.0   
60  Borough of Manhattan, New York County,New York...     191.0   
61                                      New York City     140.0   
62                             New York City,Brooklyn     215.0   

                  access_id  \
0                 1621_HPBL   
1                       NaN   
2                       NaN   
3                       NaN   
4                       501   
..                      ...   
58                      NaN   
59                      NaN   
60  910, 163, 016, 641, 755   
61                     1749   
62        16, 752, 031, 621   

                                               source  ... access_type_other  \
0                                              Lowe's  ...               NaN   
1                                                 NaN  ...               NaN   
2                                                 NaN  ...               NaN   
3                                                 NaN  ...               NaN   
4                                              Queens  ...         marshland   
..                                                ...  ...               ...   
58                                                NaN  ...               NaN   
59                                                NaN  ...               NaN   
60  watertrails,nyc water trail,nyc wap hpb,nyc wa...  ...               NaN   
61                                       nyc wap fish  ...        Promenade    
62                       nyc wap hpb,,nyc water trail  ...         Promenade   

   water_depth_est                           water_quality_monitoring  \
0              NaN  https://www.riverkeeper.org/water-quality/huds...   
1

#### Function to create new act_codes based on Alyssa's YN columns

 - if none are defined as Y, then act_codes == VISUAL
 - discuss with Sara E, we decided to define them all as FISH, but when I looked at them it didn;t seem right

In [159]:
def create_new_act_codes(row):
    activities = []
    if row['FISH_YN'] == 'Y':
        activities.append('FISH')
    if row['SWIM_YN'] == 'Y':
        activities.append('SWIM')
    if row['HPBL_YN'] == 'Y':
        activities.append('HPBL')
    if row['MPBL_YN'] == 'Y':
        activities.append('MPBL')
        
    if not activities:
        activities.append('VISUAL')
    
    return ','.join(activities)

#### Handle new sites

 - create dataframe of sites that aren't in the existing dataset
 - add source info
 - add site_id
 - check and update act_codes

In [160]:
# add site_id to all the new sites

new_sites = (
    raw_surv_new
    .query("site_id.isna()")
    .assign(
        source = "Alyssa, summer 23 new site"
    )
    .reset_index(drop=True)
)

new_sites['site_id'] = new_sites.index + highest ### the highest site_id (other than one that ends in 999 for a specific reason, is 900136)

In [161]:
new_sites['act_codes'] = new_sites.apply(create_new_act_codes, axis=1)

new_sites

ObjectID                              GlobalID county  lat  lon  \
0         36  26b60cc7-0f57-49f6-8efa-e16ec0ddf0a2    NaN  NaN  NaN   
1         37  a0ac502e-6ea8-4c64-8ef5-c0e1ff10665e    NaN  NaN  NaN   
2         38  b9a61410-d38b-4e79-88ee-cfc5f723fb58    NaN  NaN  NaN   
3         41  6095d94b-8a52-4368-8a99-1f2088a690f0    NaN  NaN  NaN   
4         44  4fe69fc5-ce1e-4e3d-86f2-c08ee115b7d3    NaN  NaN  NaN   
5         45  45838631-7518-41eb-88ed-83f029354329    NaN  NaN  NaN   
6         46  df04d5fe-95b2-44ad-8d6c-1a3dd770f31f    NaN  NaN  NaN   
7         47  5e0fd162-5841-4784-8510-7786ef285ce4    NaN  NaN  NaN   
8         53  50241fa8-f460-42e5-8cf4-3551107853d1    NaN  NaN  NaN   
9         56  7fd1fede-5f52-4c57-85bb-206accf6490c    NaN  NaN  NaN   
10        57  6101c1a0-d8f7-4854-8034-9bb337ec231e    NaN  NaN  NaN   
11        58  ce0c11d9-c208-47be-8ea0-6c85319c077a    NaN  NaN  NaN   
12        59  34e95d22-a291-4777-86bf-2081c92aa57a    NaN  NaN  NaN   
13        69  0b7ff548-4293-4917-80df-0a5261ad4e87    NaN  NaN  NaN   
14        73  646082d3-b9ef-428d-8b9d-c42cd1579146    NaN  NaN  NaN   
15        74  19e0ff53-5d54-4f97-8891-7b98406ca32b    NaN  NaN  NaN   
16        77  482fbcba-eb0b-49d0-8fb0-e9b93cdb7350    NaN  NaN  NaN   
17        83  114e1e2d-adfb-4fae-8f98-af66f9af1eb7    NaN  NaN  NaN   
18        84  9c57ddf2-5ccf-49f3-8619-0f6db582133e    NaN  NaN  NaN   
19        85  a5b8766b-8790-48d4-81ad-5226d74e97c2    NaN  NaN  NaN   
20        87  d5cb0907-a8b8-4f7f-898e-b369efad311d    NaN  NaN  NaN   
21        91  c6ff416f-26a3-49a0-8bd9-8217625b215e    NaN  NaN  NaN   
22        94  c48c5370-3e9c-489f-8808-b2047c3e5575    NaN  NaN  NaN   

   municipality natural_no  site_id access_id                      source  \
0           NaN        NaN   900136       NaN  Alyssa, summer 23 new site   
1           NaN        NaN   900137       NaN  Alyssa, summer 23 new site   
2           NaN        NaN   900138       NaN  Alyssa, summer 23 new site   
3           NaN        NaN   900139       NaN  Alyssa, summer 23 new site   
4           NaN        NaN   900140       NaN  Alyssa, summer 23 new site   
5           NaN        NaN   900141       NaN  Alyssa, summer 23 new site   
6           NaN        NaN   900142       NaN  Alyssa, summer 23 new site   
7           NaN        NaN   900143       NaN  Alyssa, summer 23 new site   
8           NaN        NaN   900144       NaN  Alyssa, summer 23 new site   
9           NaN        NaN   900145       NaN  Alyssa, summer 23 new site   
10          NaN        NaN   900146       NaN  Alyssa, summer 23 new site   
11          NaN        NaN   900147       NaN  Alyssa, summer 23 new site   
12          NaN        NaN   900148       NaN  Alyssa, summer 23 new site   
13          NaN        NaN   900149       NaN  Alyssa, summer 23 new site   
14          NaN        NaN   900150       NaN  Alyssa, summer 23 new site   
15          NaN        NaN   900151       NaN  Alyssa, summer 23 new site   
16          NaN        NaN   900152       NaN  Alyssa, summer 23 new site   
17          NaN        NaN   900153       NaN  Alyssa, summer 23 new site   
18          NaN        NaN   900154       NaN  Alyssa, summer 23 new site   
19          NaN        NaN   900155       NaN  Alyssa, summer 23 new site   
20          NaN        NaN   900156       NaN  Alyssa, summer 23 new site   
21          NaN        NaN   900157       NaN  Alyssa, summer 23 new site   
22          NaN        NaN   900158       NaN  Alyssa, summer 23 new site   

    ... access_type_other water_depth_est  \
0   ...               NaN             NaN   
1   ...               NaN             NaN   
2   ...               NaN             NaN   
3   ...               NaN             NaN   
4   ...               NaN             NaN   
5   ...               NaN             NaN   
6   ...               NaN             NaN   
7   ...               NaN             NaN   
8   ...     Floating Lab              NaN   


#### Handle updated sites

 - create dataframe of sites that are in the existing dataset
 - add spource info
 - create dataframe of information in old hap_site_points to check if there are any issues
 - check and update act_codes

In [162]:
## create a dataframe of updated site_ids 

updated_sites = (
    raw_surv_new
    .query("site_id.notna()")
    .assign(
        source = "Alyssa, summer 23 updated site",
        act_codes = raw_surv_new.apply(create_new_act_codes, axis=1)
    )
    # .filter(['site_id', 'site_name'], axis="columns") # first look at the names to check
)

#updated_sites
updated_sites['site_id'] = updated_sites['site_id'].astype(float)
site_points_df['site_id'] = site_points_df['site_id'].astype(float)

# this is the old sites, can use this to compare later
replaced_sites = site_points_df.merge(updated_sites[['site_id']], on='site_id', how='inner')

# explored in the console
# len(updated_sites) 
# = 39
# len(replaced_sites) 
# = 39
### there is a dupe in the original data, I will make sure it is removed when I bind all the dfs togther

### Create a global id - site id key for new sites to add activity points

In [163]:
### create global id - site id key to join activity point locations added in survey to the current activity points
updated_temp = updated_sites[['GlobalID', 'site_id', 'site_name']].copy()
new_temp = new_sites[['GlobalID', 'site_id', 'site_name']].copy()
global_key = pd.concat([updated_temp, new_temp], ignore_index=True)
global_key

GlobalID   site_id  \
0   2446f541-de5b-4b1b-84d0-973d1f66cf4b   71975.0   
1   29390baf-6222-415a-8ec2-2a8b8024c3d9  649119.0   
2   1529e54f-04f9-4e20-8206-3a67ea8e3f98      45.0   
3   da1362e6-2cd3-4d8e-8248-83e909a7604e     194.0   
4   acca971b-396f-448a-8e8f-e0b66097472e     161.0   
..                                   ...       ...   
58  9c57ddf2-5ccf-49f3-8619-0f6db582133e  900154.0   
59  a5b8766b-8790-48d4-81ad-5226d74e97c2  900155.0   
60  d5cb0907-a8b8-4f7f-898e-b369efad311d  900156.0   
61  c6ff416f-26a3-49a0-8bd9-8217625b215e  900157.0   
62  c48c5370-3e9c-489f-8808-b2047c3e5575  900158.0   

                               site_name  
0   Lowe's Gowanus Parklet & Boat Launch  
1            Shirley Chisholm State Park  
2           Canarsie Pier at Jamaica Bay  
3                   Bay Ridge Kite Field  
4                        Shore Road Park  
..                                   ...  
58                   St Croix by the Sea  
59             Bay View at Bayfield Ave   
60                         Seaway Marina  
61             Peter Jay Sharp Boathouse  
62                        Dyckman Marina  

[63 rows x 3 columns]

## Create updated hap_site_points

 - use antijoin to remove the sites that have been updated
 - concat to combine old, updated, and new

In [164]:
# antijoin
sites_no_update = site_points_df.merge(updated_sites[['site_id']], how='left', indicator=True).query('_merge == "left_only"').drop('_merge', axis="columns")

### test to determine if the antijoin worked as predicted, should == 0
len(site_points_df) - len(replaced_sites) - len(sites_no_update)

0

In [166]:
new_hap_site_points_temp = pd.concat([sites_no_update, updated_sites], ignore_index=True)

#### check to make sure these are the same length

len(new_hap_site_points_temp)
#len(current_site_points)
# 752 - remove rockaways and remove dupes

748

In [131]:
new_hap_site_points = pd.concat([new_hap_site_points_temp, new_sites], ignore_index=True)
# len(new_hap_site_points)
#len(current_site_points) + len(new_sites)
# 785 = correct after removing one rockaways site

### Checks to ensure that the new data will work with the website

 - act_codes have no spaces
 - all sites have act_codes
 - all sites have site_id

In [132]:
### remove spaces in the act_codes

new_hap_site_points['act_codes'] = new_hap_site_points['act_codes'].str.replace(r'\s*,\s*', ',')

### update lat and long
new_hap_site_points['lat'] = new_hap_site_points['y']
new_hap_site_points['lon'] = new_hap_site_points['x']


In [49]:
### check for spaces or NAs - will need to figure out what to do about VISUAL and STE

new_hap_site_points['act_codes'].unique()

array(['FISH,HPBL,MPBL', 'MPBL,HPBL,FISH', 'FISH', 'HPBL', 'HPBL,MPBL',
       'MPBL', 'SWIM', 'HPBL,FISH', 'MPBL,FISH', 'MPBL,HPBL', 'FISH,SWIM',
       'FISH,HPBL', 'MPBL,FISH,SWIM,HPBL', 'HPBL,MPBL,FISH',
       'MPBL,HPBL,FISH,SWIM', 'FISH,MPBL,HPBL', 'FISH,MPBL', 'SWIM,FISH',
       'HPBL,SWIM,MPBL', 'MPBL,SWIM', 'HPBL,FISH,MPBL',
       'MPBL,HPBL,SWIM,FISH', 'MPBL,SWIM,HPBL,FISH',
       'SWIM,MPBL,HPBL,FISH', 'HPBL,SWIM,FISH', 'SWIM,FISH,HPBL',
       'HPBL,SWIM', 'MPBL,FISH,HPBL', 'FISH,SWIM,MPBL,HPBL',
       'FISH,MPBL,HPBL,SWIM', 'MPBL,FISH,SWIM', 'VISUAL', 'SWIM,HPBL'],
      dtype=object)

In [133]:
### count the NA site_ids

new_hap_site_points['site_id'].isna().sum() 

0

In [134]:
new_hap_site_points

site_id       act_codes                             access_id  \
0       174.0  FISH,HPBL,MPBL                      4, 516, 151, 787   
1        29.0  MPBL,HPBL,FISH                   126, 83, 1613, 1803   
2       183.0            FISH                      1, 443, 511, 800   
3        54.0  MPBL,HPBL,FISH     291, 433, 293, 166, 117, 000, 000   
4         1.0            HPBL  9, 097, 941, 594, 168, 710, 000, 000   
..        ...             ...                                   ...   
779  900167.0            FISH                                   NaN   
780  900168.0            FISH                                   NaN   
781  900169.0            MPBL                                   NaN   
782  900170.0            HPBL                                   NaN   
783  900171.0            MPBL                                   NaN   

                     site_name           site_label  \
0               Bayswater Park                 None   
1        Conference House Park                 None   
2      Mt Loretto Natural Area                 None   
3             Lemon Creek Park                 None   
4               Riverside Park                 None   
..                         ...                  ...   
779        St Croix by the Sea                  NaN   
780  Bay View at Bayfield Ave                   NaN   
781              Seaway Marina  Thursby Ave Marina    
782  Peter Jay Sharp Boathouse                  NaN   
783             Dyckman Marina                  NaN   

                                          site_address  \
0    Dwight Ave, Seagirt Blvd between Beach 38th St...   
1    Hylan Blvd & Satterlee St, Staten Island, Hyla...   
2    End of Sharrotts Ave at Hylan Blvd, Hylan Blvd...   
3                                                 None   
4                             W 79th St End, Manhattan   
..                                                 ...   
779   Bayfield Ave and Beach 65th St, Queens, NY 11692   
780            799-701 Beach 69th St, Queens, NY 11692   
781                 7246 Thursby Ave, Queens, NY 11692   
782           3579 Harlem River Dr, New York, NY 10034   
783                 348 Dyckman St, New York, NY 10034   

                                      site_description  \
0    This waterfront park is named, in part, for Ju...   
1    The site of a legendary display of American de...   
2                                                 None   
3                             Yellow trail nature path   
4    This site is considered a cultural resource. R...   
..                                                 ...   
779  St Croix by the Sea is a community-based water...   
780  Located at the end of Beach 69th Street in the...   
781                                                NaN   
782  The Peter Jay Sharp Boathouse is one of three ...   
783  Dyckman Marina is a public marina located in I...   

                                    hours_info  \
0    Sunrise to Sunset (April 1 to December 1)   
1    Sunrise to Sunset (April 1 to December 1)   
2                                         None   
3                                         None   
4    Sunrise to Sunset (April 1 to December 1)   
..                                         ...   
779                                        NaN   
780                               Dawn to Dusk   
781                                        NaN   
782                          7:00 am - 1:00 pm   
783                                        NaN   

                                       open_close_date   fee  ...  \
0                                                 None  None  ...   
1                                                 None     Y  ...   
2                                                 None  None  ...   
3                                                 None  None  ...   
4                                                 None  None  ...   
..                                                 ...   ...  ...   
779           

## Create spatial dataframe

 - make map; red points are new or updated

In [135]:
hap_site_points = gpd.GeoDataFrame(new_hap_site_points, geometry=gpd.points_from_xy(new_hap_site_points['x'], new_hap_site_points['y']), crs="EPSG:4326")

In [136]:
m = folium.Map(
    location=[
        hap_site_points['y'].mean(), 
        hap_site_points['x'].mean()
    ], 
    zoom_start=10,
)

#creating a Marker for each point in df_sample. Each point will get a popup with their zip
for row in hap_site_points.itertuples():
        popup_text = f"Site Name: {row.site_name}<br>Activity Codes: {row.act_codes}"
        color = 'blue' if pd.isna(row.Creator) else 'red'
    
        folium.CircleMarker(
            location=[row.y,  row.x],
            radius=4,
            popup=popup_text,
            color=color,  # Change the color of the circle outline
            fill=True,
            fill_color='blue'
        ).add_to(m)
    
m   

### write out the geojson

In [137]:
#hap_site_points.to_file('data/hap_site_points_20230906.geojson', driver='GeoJSON')

### Import acitivity points to update with new survey data

In [138]:
current_act_points = gpd.read_file('data/hap_act_points_20230815_2.geojson')

act_points = (
    current_act_points
    .query("site_id != '160223'") 
    .assign(
        lon = current_act_points['geometry'].apply(lambda geom: geom.x),
        lat = current_act_points['geometry'].apply(lambda geom: geom.y)
    )
    .drop(columns=['geometry'])
     [['act_id', 'access_id', 'site_id', 'site_name', 'activity', 'access_name', 'lon', 'lat']]
)
act_points

act_id  access_id site_id                       site_name activity  \
0     1453_FISH     1453.0  501734             1st St & W River Rd     FISH   
1     1452_FISH     1452.0  501120             2nd St & William St     FISH   
2     1451_FISH     1451.0  501108             3rd St & William St     FISH   
3      937_FISH      937.0  286080          911 Memorial Weehawken     FISH   
4     1790_FISH     1790.0  181010  Fishing access off Seagirt Ave     FISH   
...         ...        ...     ...                             ...      ...   
1153  1827_FISH     1827.0     192            Hallett's Cove Beach     FISH   
1154  1828_HPBL     1828.0  900124      Hudson River Park, Pier 26     HPBL   
1155  1829_FISH     1829.0  900124      Hudson River Park, Pier 26     FISH   
1156  1830_MPBL     1830.0  645755              Yonkers Yacht Club     MPBL   
1157  1831_HPBL     1831.0  645755              Yonkers Yacht Club     HPBL   

                         access_name        lon        lat  
0                1st St & W River Rd -74.014337  40.375910  
1                2nd St & William St -74.015138  40.375671  
2                3rd St & William St -74.016032  40.375349  
3             911 Memorial Weehawken -74.010929  40.772841  
4     Fishing access off Seagirt Ave -73.741771  40.595561  
...                              ...        ...        ...  
1153            Hallett's Cove Beach -73.935281  40.769618  
1154   Downtown Boathouse at Pier 26 -74.012820  40.721259  
1155                         Pier 26 -74.015336  40.721399  
1156              Yonkers Yacht Club -73.888117  40.977102  
1157              Yonkers Yacht Club -73.888130  40.977122  

[1157 rows x 8 columns]

In [139]:
## add new survey data
raw_surv_act_new = pd.read_csv('data/staging/activity_loc_point_1.csv')

In [140]:
raw_surv_act_new

ObjectID                              GlobalID  \
0         45  38914c86-724a-40ab-85fe-cbfe7480cb66   
1         48  e69eef4e-3808-4843-81c3-7ffe4eadbaae   
2         49  0d0f0ec4-9469-47af-8555-f878d34e4fc4   
3         51  572e6db3-43f1-4b29-818a-f9aacd3b149e   
4         52  37406c77-eb81-4e23-83b0-789e22af0ab5   
..       ...                                   ...   
71       122  ca912182-958a-47b0-8db1-084593880cf7   
72       123  3abad9f8-f055-4d3c-835f-fbf31f18adb8   
73       124  65483e92-f8d0-4b05-8c02-38a3a8c8f738   
74       125  0970e74c-0a05-4df1-8313-8bc02c72a18a   
75       126  c8865986-999e-479e-883e-dd925172c8a1   

                               access_name  access_address  \
0   Lowe's Gowanus Parklet and Boat Launch             NaN   
1                                      NaN             NaN   
2                                      NaN             NaN   
3                      Hendrix Creek Pier              NaN   
4                                      NaN             NaN   
..                                     ...             ...   
71                   Fort Washington Park              NaN   
72                       West Harlem Piers             NaN   
73                       West Harlem Piers             NaN   
74         Harlem River Park and Greenway              NaN   
75               Gowanus Canal Sponge Park             NaN   

                          ParentGlobalID    CreationDate  \
0   2446f541-de5b-4b1b-84d0-973d1f66cf4b  7/9/2023 12:58   
1   a0ac502e-6ea8-4c64-8ef5-c0e1ff10665e  7/9/2023 14:38   
2   a0ac502e-6ea8-4c64-8ef5-c0e1ff10665e  7/9/2023 14:38   
3   29390baf-6222-415a-8ec2-2a8b8024c3d9  7/9/2023 19:20   
4   29390baf-6222-415a-8ec2-2a8b8024c3d9  7/9/2023 19:20   
..                                   ...             ...   
71  61f4f63a-7622-4267-8ca0-cb36872d2afb  9/1/2023 18:34   
72  3909c237-197f-453e-8211-0d6454d25dbf  9/1/2023 18:57   
73  3909c237-197f-453e-8211-0d6454d25dbf  9/1/2023 18:57   
74  0bebe570-9c68-42ee-8040-c98ffb8e61ce  9/1/2023 19:12   
75  e1813fbf-48fa-45aa-85b6-be539e5a2937  9/1/2023 21:57   

                          Creator         EditDate  \
0                   abement_Pratt  7/28/2023 20:14   
1                   abement_Pratt   7/9/2023 14:38   
2                   abement_Pratt   7/9/2023 14:38   
3                   abement_Pratt   7/9/2023 19:20   
4                   abement_Pratt   7/9/2023 19:20   
..                            ...              ...   
71  HudsonAccessProject_PrattSAVI   9/1/2023 18:34   
72  HudsonAccessProject_PrattSAVI   9/1/2023 18:57   
73  HudsonAccessProject_PrattSAVI   9/1/2023 18:57   
74  HudsonAccessProject_PrattSAVI   9/1/2023 19:12   
75  HudsonAccessProject_PrattSAVI   9/1/2023 21:57   

                           Editor act_code          x          y  
0   HudsonAccessProject_PrattSAVI     HPBL -73.996945  40.673120  
1                   abement_Pratt     HPBL -74.018112  40.678672  
2                   abement_Pratt     FISH -74.019597  40.678400  
3                   abement_Pratt     HPBL -73.873679  40.645966  
4                   abement_Pratt     HPBL -73.857275  40.644370  
..                            ...      ...        ...        ...  
71  HudsonAccessProject_PrattSAVI     FISH -73.938707  40.858496  
72  HudsonAccessProject_PrattSAVI     HPBL -73.959784  40.820668  
73  HudsonAccessProject_PrattSAVI     FISH -73.961136  40.819490  
74  HudsonAccessProject_PrattSAVI     FISH -73.934076  40.812595  
75  HudsonAccessProject_PrattSAVI     HPBL -73.990020  40.676683  

[76 rows x 12 columns]

In [141]:
# this is the old sites, can use this to compare later
survey_acts = (
    raw_surv_act_new
    .merge(global_key, left_on='ParentGlobalID', right_on='GlobalID', how='left')
)

survey_acts = (
    survey_acts
    .assign(
        activity = survey_acts.apply(lambda row: row['act_codes'] if pd.isna(row['act_code']) else row['act_code'], axis=1),
        access_name = survey_acts.apply(lambda row: row['site_name'] if pd.isna(row['access_name']) else row['access_name'], axis=1),
        access_id = survey_acts.index + 1800, ### the highest 
    )
    .rename(columns={'x': 'lon', 'y': 'lat'})
     [['access_id', 'site_id', 'site_name', 'activity', 'access_name', 'lon', 'lat']]
)

survey_acts['act_id'] = survey_acts.apply(lambda row: f"{row['access_id']}_{row['activity']}", axis=1)

survey_acts

access_id   site_id                             site_name activity  \
0        1800   71975.0  Lowe's Gowanus Parklet & Boat Launch     HPBL   
1        1801  900150.0               Louis Valentino Jr Park     HPBL   
2        1802  900150.0               Louis Valentino Jr Park     FISH   
3        1803  649119.0           Shirley Chisholm State Park     HPBL   
4        1804  649119.0           Shirley Chisholm State Park     HPBL   
..        ...       ...                                   ...      ...   
71       1871      62.0                  Fort Washington Park     FISH   
72       1872     191.0                West Harlem Piers Park     HPBL   
73       1873     191.0                West Harlem Piers Park     FISH   
74       1874     140.0        Harlem River Park and Greenway     FISH   
75       1875     215.0             Gowanus Canal Sponge Park     HPBL   

                               access_name        lon        lat     act_id  
0   Lowe's Gowanus Parklet and Boat Launch -73.996945  40.673120  1800_HPBL  
1                  Louis Valentino Jr Park -74.018112  40.678672  1801_HPBL  
2                  Louis Valentino Jr Park -74.019597  40.678400  1802_FISH  
3                      Hendrix Creek Pier  -73.873679  40.645966  1803_HPBL  
4              Shirley Chisholm State Park -73.857275  40.644370  1804_HPBL  
..                                     ...        ...        ...        ...  
71                   Fort Washington Park  -73.938707  40.858496  1871_FISH  
72                       West Harlem Piers -73.959784  40.820668  1872_HPBL  
73                       West Harlem Piers -73.961136  40.819490  1873_FISH  
74         Harlem River Park and Greenway  -73.934076  40.812595  1874_FISH  
75               Gowanus Canal Sponge Park -73.990020  40.676683  1875_HPBL  

[76 rows x 8 columns]

### Check for existing activity points that are being updated and remove them from current list

In [142]:
# perform a full join of current activity points and the survey activity points and select the activities that are in both
# these will be removed from current and replaced by the surey

# Convert 'site_id' to object data type in both DataFrames
survey_acts['site_id'] = survey_acts['site_id'].astype(float)
current_act_points['site_id'] = current_act_points['site_id'].astype(float)
act_points['site_id'] = act_points['site_id'].astype(float)

updated_activity_points = (
    survey_acts
    .merge(current_act_points, on=['site_id', 'activity'], how='outer', indicator=True)
     .query('_merge == "both"')
    [['site_id', 'activity']]
)

updated_activity_points

site_id activity
0    71975.0     HPBL
3   649119.0     HPBL
4   649119.0     HPBL
5   649119.0     HPBL
6   649119.0     HPBL
..       ...      ...
86     191.0     FISH
87     140.0     FISH
88     215.0     HPBL
89     215.0     HPBL
90     215.0     HPBL

[63 rows x 2 columns]

In [143]:
## perform a full join with list of activities to remove, remove merge = both

new_act_points_temp = (
    act_points
    .merge(updated_activity_points, on=['site_id', 'activity'], how='outer', indicator=True)
    .query('_merge == "left_only"')
    .drop(columns=['_merge'])
)
new_act_points_temp

act_id  access_id   site_id                        site_name  \
0     1453_FISH     1453.0  501734.0              1st St & W River Rd   
1     1452_FISH     1452.0  501120.0              2nd St & William St   
2     1451_FISH     1451.0  501108.0              3rd St & William St   
3      937_FISH      937.0  286080.0           911 Memorial Weehawken   
4     1790_FISH     1790.0  181010.0   Fishing access off Seagirt Ave   
...         ...        ...       ...                              ...   
1159  1802_FISH     1802.0     157.0          Louis Valentino Jr Park   
1172  1809_FISH     1809.0  900141.0                    Canarsie Park   
1182  1813_FISH     1813.0  900137.0  American Veterans Memorial Pier   
1191  1822_FISH     1822.0  900138.0                 Bensonhurst Park   
1192  1823_FISH     1823.0  900148.0       Pier 44 Waterfront Garden    

     activity                      access_name        lon        lat  
0        FISH              1st St & W River Rd -74.014337  40.375910  
1        FISH              2nd St & William St -74.015138  40.375671  
2        FISH              3rd St & William St -74.016032  40.375349  
3        FISH           911 Memorial Weehawken -74.010929  40.772841  
4        FISH   Fishing access off Seagirt Ave -73.741771  40.595561  
...       ...                              ...        ...        ...  
1159     FISH          Louis Valentino Jr Park -74.019597  40.678400  
1172     FISH                    Canarsie Park -73.895239  40.622942  
1182     FISH  American Veterans Memorial Pier -74.038560  40.639621  
1191     FISH                 Bensonhurst Park -74.002562  40.594902  
1192     FISH   Pier 44 Waterfront Garden Pier -74.018508  40.675365  

[1098 rows x 8 columns]

In [144]:
### add the new points to the old points and make access name site name if it is na

new_act_points = pd.concat([new_act_points_temp, survey_acts], ignore_index=True)

new_act_points['access_name'] = new_act_points.apply(lambda row: row['site_name'] if pd.isna(row['access_name']) else row['access_name'], axis=1)

new_act_points

act_id  access_id   site_id                       site_name activity  \
0     1453_FISH     1453.0  501734.0             1st St & W River Rd     FISH   
1     1452_FISH     1452.0  501120.0             2nd St & William St     FISH   
2     1451_FISH     1451.0  501108.0             3rd St & William St     FISH   
3      937_FISH      937.0  286080.0          911 Memorial Weehawken     FISH   
4     1790_FISH     1790.0  181010.0  Fishing access off Seagirt Ave     FISH   
...         ...        ...       ...                             ...      ...   
1169  1871_FISH     1871.0      62.0            Fort Washington Park     FISH   
1170  1872_HPBL     1872.0     191.0          West Harlem Piers Park     HPBL   
1171  1873_FISH     1873.0     191.0          West Harlem Piers Park     FISH   
1172  1874_FISH     1874.0     140.0  Harlem River Park and Greenway     FISH   
1173  1875_HPBL     1875.0     215.0       Gowanus Canal Sponge Park     HPBL   

                          access_name        lon        lat  
0                 1st St & W River Rd -74.014337  40.375910  
1                 2nd St & William St -74.015138  40.375671  
2                 3rd St & William St -74.016032  40.375349  
3              911 Memorial Weehawken -74.010929  40.772841  
4      Fishing access off Seagirt Ave -73.741771  40.595561  
...                               ...        ...        ...  
1169            Fort Washington Park  -73.938707  40.858496  
1170                West Harlem Piers -73.959784  40.820668  
1171                West Harlem Piers -73.961136  40.819490  
1172  Harlem River Park and Greenway  -73.934076  40.812595  
1173        Gowanus Canal Sponge Park -73.990020  40.676683  

[1174 rows x 8 columns]

## make geospatial activity points

In [147]:
hap_act_points = gpd.GeoDataFrame(new_act_points, geometry=gpd.points_from_xy(new_act_points['lon'], new_act_points['lat']), crs="EPSG:4326")
#hap_act_points = hap_act_points.drop(columns=['lon', 'lat'])

hap_act_points

act_id  access_id   site_id                       site_name activity  \
0     1453_FISH     1453.0  501734.0             1st St & W River Rd     FISH   
1     1452_FISH     1452.0  501120.0             2nd St & William St     FISH   
2     1451_FISH     1451.0  501108.0             3rd St & William St     FISH   
3      937_FISH      937.0  286080.0          911 Memorial Weehawken     FISH   
4     1790_FISH     1790.0  181010.0  Fishing access off Seagirt Ave     FISH   
...         ...        ...       ...                             ...      ...   
1169  1871_FISH     1871.0      62.0            Fort Washington Park     FISH   
1170  1872_HPBL     1872.0     191.0          West Harlem Piers Park     HPBL   
1171  1873_FISH     1873.0     191.0          West Harlem Piers Park     FISH   
1172  1874_FISH     1874.0     140.0  Harlem River Park and Greenway     FISH   
1173  1875_HPBL     1875.0     215.0       Gowanus Canal Sponge Park     HPBL   

                          access_name        lon        lat  \
0                 1st St & W River Rd -74.014337  40.375910   
1                 2nd St & William St -74.015138  40.375671   
2                 3rd St & William St -74.016032  40.375349   
3              911 Memorial Weehawken -74.010929  40.772841   
4      Fishing access off Seagirt Ave -73.741771  40.595561   
...                               ...        ...        ...   
1169            Fort Washington Park  -73.938707  40.858496   
1170                West Harlem Piers -73.959784  40.820668   
1171                West Harlem Piers -73.961136  40.819490   
1172  Harlem River Park and Greenway  -73.934076  40.812595   
1173        Gowanus Canal Sponge Park -73.990020  40.676683   

                        geometry  
0     POINT (-74.01434 40.37591)  
1     POINT (-74.01514 40.37567)  
2     POINT (-74.01603 40.37535)  
3     POINT (-74.01093 40.77284)  
4     POINT (-73.74177 40.59556)  
...                          ...  
1169  POINT (-73.93871 40.85850)  
1170  POINT (-73.95978 40.82067)  
1171  POINT (-73.96114 40.81949)  
1172  POINT (-73.93408 40.81259)  
1173  POINT (-73.99002 40.67668)  

[1174 rows x 9 columns]

In [151]:
act_m = folium.Map(
    location=[
        hap_act_points['lat'].mean(), 
        hap_act_points['lon'].mean()
    ], 
    zoom_start=10,
)

#creating a Marker for each point in df_sample. Each point will get a popup with their zip
for row in hap_act_points.itertuples():
        popup_text = f"Site Name: {row.site_name}<br>Activity Codes: {row.activity}"
#         color = 'blue' if pd.isna(row.Creator) else 'red'
    
        folium.CircleMarker(
            location=[row.lat,  row.lon],
            radius=4,
            popup=popup_text,
            color='blue',  # Change the color of the circle outline
            fill=True,
            fill_color='blue'
        ).add_to(act_m)
    
# act_m 

## check for sites with no activity points

In [152]:
# site_activity
site_activity_join = (
    hap_site_points[['site_id', 'site_name', 'source']]
    .rename(columns={'site_name': 'site_name_site'})
    .merge(hap_act_points, on='site_id', how='outer')
)

# no_acts
no_acts = site_activity_join[site_activity_join['act_id'].isna()]

no_acts
### there are 17

site_id                               site_name_site  \
18    109392.0                          Brooklyn Yacht Club   
62    147570.0                           Pilgrim Yacht Club   
63    147662.0                          Flamingo Yacht Club   
1073  900139.0                   Brooklyn Bay Center at BJs   
1074  900140.0                     Bush Terminal Piers Park   
1076  900142.0                     Empire City Water Sports   
1077  900143.0        Fairway Promenade at Red Hook Stores    
1078  900144.0                       Greenpoint Public Park   
1079  900145.0                            Lowlands Nursery    
1080  900146.0                                MARY A WHALEN   
1081  900147.0                    Narrows Botanical Gardens   
1083  900149.0  RETI Field Station at Gowanus Bay Terminal    
1084  900149.0        Fairway Promenade at Red Hook Stores    
1111  595580.0                  Steuben House Historic Site   
1167  900151.0                               MARY A. WHALEN   
1169  900153.0                    Narrows Botanical Gardens   
1171  900155.0                     Bush Terminal Piers Park   
1172  900156.0                       Greenpoint Public Park   
1173  900157.0  RETI Field Station at Gowanus Bay Terminal    
1174  900158.0                     Empire City Water Sports   
1175  900159.0                   Brooklyn Bay Center at BJs   
1179  900163.0                                  Bridge Park   

                              source act_id  access_id site_name activity  \
18                              None    NaN        NaN       NaN      NaN   
62                              None    NaN        NaN       NaN      NaN   
63                              None    NaN        NaN       NaN      NaN   
1073      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1074      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1076      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1077      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1078      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1079      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1080      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1081      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1083      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1084      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1111  Alyssa, summer 23 updated site    NaN        NaN       NaN      NaN   
1167      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1169      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1171      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1172      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1173      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1174      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1175      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   
1179      Alyssa, summer 23 new site    NaN        NaN       NaN      NaN   

     access_name  lon  lat geometry  
18           NaN  NaN  NaN     None  
62           NaN  NaN  NaN     None  
63           NaN  NaN  NaN     None  
1073         NaN  NaN  NaN     None  
1074         NaN  NaN  NaN     None  
1076         NaN  NaN  NaN     None  
1077         NaN  NaN  NaN     None  
1078         NaN  NaN  NaN     None  
1079         NaN  NaN  NaN     None  
1080         NaN  NaN  NaN     None  
1081         NaN  NaN  NaN     None  
1083         NaN  NaN  NaN     None  
1084         NaN  NaN  NaN     None  
1111         NaN  NaN  NaN     None  
1167         NaN  NaN  NaN     None  
1169         NaN  NaN  NaN     None  
1171         NaN  NaN  NaN     None  
1172         NaN  NaN  NaN     None  
1173         NaN  NaN  NaN     None  
1174         NaN  NaN  Na

## write out act points

In [153]:
hap_act_points.to_file('data/hap_act_points_20230906.geojson', driver='GeoJSON')